### Importing Libraries

In [1]:
# Import libraries
import numpy as np 
import pandas as pd 
import plotly as py
import plotly.express as px
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

import easygui
import pandas_profiling

In [2]:
print("Select DataSet: ")
# save filepath to variable for easier access
ds = easygui.fileopenbox()
data = pd.read_csv(ds)
data.profile_report()

Select DataSet: 


### Renaming Columns

In [3]:
data = data.rename(columns={'Country/Region':'Country'})
data = data.rename(columns={'ObservationDate':'Date'})

### Manipulate Dataframe

In [4]:
data_countries = data.groupby(['Country', 'Date']).sum().reset_index().sort_values('Date', ascending=False)
data_countries = data_countries.drop_duplicates(subset = ['Country'])
data_countries = data_countries[data_countries['Confirmed']>0]

### Create the Choropleth

In [5]:
fig = go.Figure(data=go.Choropleth(
    locations = data_countries['Country'],
    locationmode = 'country names',
    z = data_countries['Confirmed'],
    colorscale = 'Reds',
    marker_line_color = 'black',
    marker_line_width = 0.5,
))

In [6]:
fig.update_layout(
    title_text = 'Confirmed Cases as of September 13, 2020',
    title_x = 0.5,
    geo=dict(
        showframe = False,
        showcoastlines = False,
        projection_type = 'equirectangular'
    )
)

### Manipulating the original dataframe

In [7]:
data_countrydate = data[data['Confirmed']>0]
data_countrydate = data_countrydate.groupby(['Date','Country']).sum().reset_index()
data_countrydate

Date             Country     SNo  Confirmed  Deaths  Recovered
0      01/22/2020               Japan      36        2.0     0.0        0.0
1      01/22/2020               Macau      21        1.0     0.0        0.0
2      01/22/2020      Mainland China     373      547.0    17.0       28.0
3      01/22/2020         South Korea      38        1.0     0.0        0.0
4      01/22/2020              Taiwan      29        1.0     0.0        0.0
...           ...                 ...     ...        ...     ...        ...
36878  09/13/2020  West Bank and Gaza  108804    30574.0   221.0    20082.0
36879  09/13/2020      Western Sahara  108805       10.0     1.0        8.0
36880  09/13/2020               Yemen  108806     2011.0   583.0     1212.0
36881  09/13/2020              Zambia  108807    13539.0   312.0    12260.0
36882  09/13/2020            Zimbabwe  108808     7526.0   224.0     5678.0

[36883 rows x 6 columns]

### Creating the visualization

In [8]:
fig = px.choropleth(data_countrydate, 
                    locations="Country", 
                    locationmode = "country names",
                    color="Confirmed", 
                    hover_name="Country", 
                    animation_frame="Date"
                   )
fig.update_layout(
    title_text = 'Global Spread of Coronavirus',
    title_x = 0.5,
    geo=dict(
        showframe = False,
        showcoastlines = False,
    ))
fig.show()